Программка для просмотра карт по слоям данных ВЦ РАН и реанализов ORAS4 и OI ice и их разниц 

Параметры выбора:

fl_cc - файл ВЦ РАН,
fl_ia - файл реанализа для льда,
dr_oras - директория с файлами ORAS4,
year - исследуемый год,
nm - номер записи (0 - ноябрь, 1-декабрь, 2- январь, ... при nm > 11 увеличивается год реанализа, данные ВЦ РАН начинаются с ноября),
nl - номер слоя реанализа,
данные ВЦ РАН иннтерполируются на слой реанализа,
par_oras - имя переменной в реанализе,
clims - флаг применения пределов при рисовке карт. 'None' - пределы не применять, автоматический выбор пределов,
ncm - номер в cmapl, списка выбора цветовой палитры. 

In [1]:
%matplotlib
import matplotlib.pyplot as plt 
import numpy as np
from netCDF4 import Dataset as nd
import cartopy.crs as ccrs

Using matplotlib backend: Qt5Agg


ImportError: No module named cartopy.crs

In [ ]:

fl_ia = 'e:/neacc/data/in/ice_oi/icec.mnmean.nc'
dr_oras = 'e:/neacc/data/in/oras4/'
year_cc = 2001
fl_cc = 'e:/neacc/data/in/cc/' + str(year_cc) +'.nc'
nm = 2
nmo = nm + 10
if nmo >= 12:
    year_oras = year_cc + 1
    nmo -= 12
else:
    year_oras = year_cc 
par_oras = 'thetao'
nl = 5
#par_oras = 'vmod'
#clims = 'None'
clims = 'lims'
ncm = 5
cmapl = ['jet','cool','coolwarm','RdBu','seismic','bwr']

# ----------- связь переменных реанализа и данных ВЦ РАН, единицы измерения, пределы на картах ------
if par_oras == 'thetao':
    par_cc = 'temperature'
    unit = u"\u00b0"+'C'
    vmin = -1.8
    vmax = 35
elif par_oras == 'so':
    par_cc = 'salinity'
    unit = '%%'
    vmin = 0
    vmax = 35
elif par_oras == 'uo':
    par_cc = 'velocity_east'
    unit = 'm/s'
    vmin = -1.
    vmax = 1.
elif par_oras == 'vo':
    par_cc = 'velocity_north'
    unit = 'm/s'
    vmin = -1.
    vmax = 1.
elif par_oras == 'vmod':
    par_cc1 = 'velocity_east'
    par_cc2 = 'velocity_north'
    unit = 'm/s'
    vmin = -1.
    vmax = 1.
elif par_oras == 'zos':
    par_cc = 'sea_surface_height'
    unit = 'm'
    vmin = -1.5
    vmax = 1.5
par_oi = 'icec'
par_cci = 'sea_ice_area_fraction' 
if par_oras == 'vmod':
    fl_orasu = dr_oras+'uo'+'_oras4_1m_'+str(year_oras)+'_grid_1x1.nc'
    fl_orasv = dr_oras+'vo'+'_oras4_1m_'+str(year_oras)+'_grid_1x1.nc'
else:    
    fl_oras = dr_oras+par_oras+'_oras4_1m_'+str(year_oras)+'_grid_1x1.nc'

In [ ]:
# ------------ наборы данных из netcdf файлов -----------------
ds_cc = nd(fl_cc,'r')
ds_ia = nd(fl_ia,'r')
if par_oras == 'vmod':
    ds_orasu = nd(fl_orasu,'r')
    ds_orasv = nd(fl_orasv,'r')
else:    
    ds_oras = nd(fl_oras,'r')

In [ ]:
# --------------  глубины данных ВЦ и реанализа ----------------
depth_cc = ds_cc['lev'][:]
if par_oras == 'vmod':
    depth_oras = ds_orasu['depth'][:]
else:    
    depth_oras = ds_oras['depth'][:]

In [2]:
# ------------ поиск номеров слоев данных ВЦ по обе стороны выбранного слоя реанализа ----------
d_oras = depth_oras[nl]
nl_cct = 0
while depth_cc[nl_cct] < d_oras:
    nl_cc = nl_cct
    nl_cct += 1

NameError: name 'depth_oras' is not defined

In [3]:
# ---------- вычисление расстояний от слоев данных ВЦ до выбранного слоя реанализа ---------
d_cc = depth_cc[nl_cc]
d_cc1 = depth_cc[nl_cc+1]
wd = abs(d_oras - d_cc)
wd1 = abs(d_oras - d_cc1)

NameError: name 'depth_cc' is not defined

In [4]:
# ------- при нулевом расстояние задается малое значения из-за дальнейшего деления на расстояние ------
wd = max(wd,1e-6)
wd1 = max(wd1,1e-6)

NameError: name 'wd' is not defined

In [5]:
# ---------- считывание выбранных переменных из реанализа и данных ВЦ -------
if par_oras == 'vmod':
    p_oras = np.sqrt(ds_orasu['uo'][:]**2 + ds_orasv['vo'][:]**2)
    p_cc = np.sqrt(ds_cc['velocity_east'][:]**2 + ds_cc['velocity_north'][:]**2) 
else:    
    p_oras = ds_oras[par_oras][:]
    p_cc = ds_cc[par_cc][:]
ndim = p_oras.ndim
ds_cc.close()

NameError: name 'par_oras' is not defined

In [6]:
# -------- приведение данных ВЦ из долгот -180 .... 0 ... 179 в долготы 0.5, 1.5 ... 359.5 в сетке реанализа -----
p_cc_l = np.copy(p_cc)
p_cc_l[:,:,:,:180] = p_cc[:,:,:,180:]
p_cc_l[:,:,:,180:] = p_cc[:,:,:,:180]
p_cc_l0 = np.copy(p_cc)
for i in range(359):
    p_cc_l0[:,:,:,i] = (p_cc_l[:,:,:,i] + p_cc_l[:,:,:,i+1]) / 2.
p_cc_l0[:,:,:,359] = (p_cc_l[:,:,:,-1] + p_cc_l[:,:,:,0]) / 2

NameError: name 'p_cc' is not defined

In [7]:
# ------- расстояния до точек, где параметр не опреден (суша и т.п.) задается большим --------
wd_arr = np.zeros((180,360))
wd1_arr = np.zeros((180,360))
wd_arr = np.where(p_cc_l0[0,nl_cc,:] > 1000,1.e6,wd)
wd1_arr = np.where(p_cc_l0[0,nl_cc+1,:] > 1000,1.e6,wd1)

NameError: name 'p_cc_l0' is not defined

In [8]:
# ---------- интерполяция данных ВЦ на слой реанализа с учетом весов ----- 
p_cc_interp = 1 / (1 / wd_arr + 1 / wd1_arr) * (p_cc_l0[nm,nl_cc,:,:] / wd_arr + p_cc_l0[nm,nl_cc+1,:,:] / wd1_arr)

/home/igor/anaconda2/lib/python2.7/site-packages/ipykernel_launcher.py:2: RuntimeWarning: divide by zero encountered in divide
  


NameError: name 'p_cc_l0' is not defined

In [9]:
# ---------- защита от вычисленных данных по ячейкам суши -----------
p_cc_interp = np.where(p_cc_interp > 1000., np.nan, p_cc_interp)

NameError: name 'p_cc_interp' is not defined

In [13]:
# -------- сетка для рисовеи карт -----------
if par_oras == 'vmod':
    lon = ds_orasu['lon'][:]
    lat = ds_orasu['lat'][:]
    ds_orasu.close()
    ds_orasv.close()
else:
    lon = ds_oras['lon'][:]
    lat = ds_oras['lat'][:]
    ds_oras.close() 

In [14]:
# ----------- отрисовка параметра реанализа ---------
fig_oras = plt.figure()
#map_oras = plt.contourf(lon,lat,p_oras[nm,nl,:,:], cmap = 'jet')
ax = plt.axes(projection=ccrs.PlateCarree())
if clims == 'None':
    map_oras = plt.pcolormesh(lon,lat,p_oras[nmo,nl,:,:], cmap = cmapl[ncm], shading = 'auto')
else:
    map_oras = plt.pcolormesh(lon,lat,p_oras[nmo,nl,:,:], cmap = cmapl[ncm], shading = 'auto', vmin = vmin, vmax = vmax)
gl = ax.gridlines(draw_labels=True)
gl.top_labels = False
gl.right_labels = False
ax.coastlines()
ax.stock_img()    
#im_ratio = ax.shape[1]/ax.shape[0]
#plt.colorbar(orientation="horizontal", fraction=0.047*im_ratio)
cbar = plt.colorbar(orientation="horizontal")
cbar.ax.set_title(unit)
plt.title(par_oras + ', ORAS4, depth = ' + str(round(depth_oras[nl],1)) + ', month = ' + str(nmo+1) )

Text(0.5, 1.0, 'thetao, ORAS4, depth = 55.7, month = 1')

In [15]:
# ----------- отрисовка параметра данных ВЦ, интерполированного на слой реанализа  ---------
ig_cc = plt.figure()
#map_cc = plt.contourf(lon,lat,p_cc_interp, cmap = 'jet')
ax = plt.axes(projection=ccrs.PlateCarree())
if clims == 'None':
    map_cc = plt.pcolormesh(lon,lat,p_cc_interp, cmap = cmapl[ncm], shading = 'auto')
else:    
    map_cc = plt.pcolormesh(lon,lat,p_cc_interp, cmap = cmapl[ncm], shading = 'auto', vmin = vmin, vmax = vmax)
gl = ax.gridlines(draw_labels=True)
gl.top_labels = False
gl.right_labels = False
ax.coastlines()
ax.stock_img()
cbar = plt.colorbar(orientation="horizontal")
cbar.ax.set_title(unit)
plt.title(par_oras + ', NEACC, depth = ' + str(round(depth_oras[nl],1)) + ', month = ' + str(nmo+1) )

Text(0.5, 1.0, 'thetao, NEACC, depth = 55.7, month = 1')

In [16]:
# ----------- отрисовка параметра реанализа за минусом данных ВЦ, интерполированного на слой реанализа  ---------
p_diff = p_oras[nmo,nl,:] - p_cc_interp[:,:]
fig_diff = plt.figure()
#map_diff = plt.contourf(lon,lat,p_diff,cmap = 'RdBu')
ax = plt.axes(projection=ccrs.PlateCarree())
map_diff = plt.pcolormesh(lon,lat,p_diff,cmap = 'RdBu', shading = 'auto')
gl = ax.gridlines(draw_labels=True)
gl.top_labels = False
gl.right_labels = False
ax.coastlines()
ax.stock_img()    
cbar = plt.colorbar(orientation="horizontal")
cbar.ax.set_title(unit)
plt.title(par_oras + ', ORAS4-NEACC, depth = ' + str(round(depth_oras[nl],1)) + ', month = ' + str(nmo+1) )

Text(0.5, 1.0, 'thetao, ORAS4-NEACC, depth = 55.7, month = 1')